In [1]:
import os
import copy
import time
import pickle
import numpy as np
import pandas as pd
from datetime import datetime
import time
import argparse
import random
import torch
from torch import nn
from torch.utils.data import DataLoader, Dataset, Subset, random_split
from torchvision import datasets, transforms
import torchvision
from torch.autograd import Variable
from torchvision.datasets import MNIST, EMNIST
import torch.nn.functional as F
from matplotlib.pyplot import subplots
from torchvision.utils import save_image
import torch.optim as optim
from tensorboardX import SummaryWriter
seed = 42
np.random.seed(seed)
random.seed(seed)
torch.manual_seed(seed)
torch.cuda.manual_seed_all(seed)
torch.backends.cudnn.deterministic = True
bs = 100
n_epoch = 50
dim=100
#device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
writer = SummaryWriter(os.path.join('../gan', '500T1dest_fix_new-zoo_first20'))
gpu = 1
device = 1

In [2]:
def test_inference(net, testloader):
    """ Returns the test accuracy and loss.
    """
    net.eval()
    loss, total, correct = 0.0, 0.0, 0.0
    criterion = nn.CrossEntropyLoss()
    criterion.cuda(gpu)
    mnist_dim = train_dataset.train_data.size(1) * train_dataset.train_data.size(2)
    with torch.no_grad():
        for batch_idx, (images, labels) in enumerate(testloader):
            images, labels = images.cuda(gpu), labels.cuda(gpu)
            
            # Inference
            outputs = net(images)
            batch_loss = criterion(outputs, labels)
            loss += copy.deepcopy(batch_loss.item())

            # Prediction
            _, pred_labels = torch.max(outputs, 1)
            pred_labels = pred_labels.view(-1)
            correct += torch.sum(torch.eq(pred_labels, labels)).item()
            total += len(labels)
    accuracy = correct/total
    return accuracy, loss

def test_error(model, steal_model, testloader):
    model.eval()
    steal_model.eval()
    loss, total, correct = 0.0, 0.0, 0.0
    
    with torch.no_grad():
        for batch_idx, (images, labels) in enumerate(testloader):
            images, labels = images.cuda(gpu), labels.cuda(gpu)

            # Inference
            outputs0 = model(images)
            outputs1 = steal_model(images)
            
            # Prediction
            _, pred_labels0 = torch.max(outputs0, 1)
            pred_labels0 = pred_labels0.view(-1)
            
            _, pred_labels1 = torch.max(outputs1, 1)
            pred_labels1 = pred_labels1.view(-1)
            
            correct += torch.sum(torch.eq(pred_labels0, pred_labels1)).item()
            total += len(labels)
    accuracy = correct/total
    return accuracy


def stat_num(model, steal_model, testloader):
    model.eval()
    steal_model.eval()
    loss, total, correct = 0.0, 0.0, 0.0
    l2n = {i: 0 for i in range(11)}
    with torch.no_grad():
        for batch_idx, (images, labels) in enumerate(testloader):
            images, labels = images.cuda(gpu), labels.cuda(gpu)

            # Inference
            outputs0 = model(images)
            outputs1 = steal_model(images)
            
            # Prediction
            _, pred_labels0 = torch.max(outputs0, 1)
            pred_labels0 = pred_labels0.view(-1)
            
            _, pred_labels1 = torch.max(outputs1, 1)
            pred_labels1 = pred_labels1.view(-1)
            
            list0 = pred_labels0.cpu().numpy().tolist()
            list1 = pred_labels1.cpu().numpy().tolist()
            for i in range(len(list0)):
                if list0[i] == list1[i]:
                    l2n[list0[i]] += 1
    for k, v in l2n.items():
        print(f"Label {k}: {v}")

class Discriminator(nn.Module):
    """
        Convolutional Discriminator for MNIST
    """
    def __init__(self, in_channel=1, num_classes=11):
        super(Discriminator, self).__init__()
        self.conv = nn.Sequential(
            # 28 -> 14
            nn.Conv2d(in_channel, 512, 3, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(512),
            nn.LeakyReLU(0.2),
            # 14 -> 7
            nn.Conv2d(512, 256, 3, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(256),
            nn.LeakyReLU(0.2),
            # 7 -> 4
            nn.Conv2d(256, 128, 3, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(128),
            nn.LeakyReLU(0.2),
            nn.AvgPool2d(4),
        )
        self.fc = nn.Sequential(
            # reshape input, 128 -> 1
            nn.Linear(128, num_classes)
        )
    
    def forward(self, x, y=None):
        y_ = self.conv(x)
        y_ = y_.view(y_.size(0), -1)
        y_ = self.fc(y_)
        return y_


class Generator(nn.Module):
    """
        Convolutional Generator for MNIST
    """
    def __init__(self, input_size=100, num_classes=784):
        super(Generator, self).__init__()
        self.fc = nn.Sequential(
            nn.Linear(input_size, 4*4*512),
            nn.ReLU(),
        )
        self.conv = nn.Sequential(
            # input: 4 by 4, output: 7 by 7
            nn.ConvTranspose2d(512, 256, 3, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            # input: 7 by 7, output: 14 by 14
            nn.ConvTranspose2d(256, 128, 4, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            # input: 14 by 14, output: 28 by 28
            nn.ConvTranspose2d(128, 1, 4, stride=2, padding=1, bias=False),
            nn.Tanh(),
        )
        
    def forward(self, x, y=None):
        x = x.view(x.size(0), -1)
        y_ = self.fc(x)
        y_ = y_.view(y_.size(0), 512, 4, 4)
        y_ = self.conv(y_)
        return y_


In [3]:
transform = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize(mean=(0.5,), std=(0.5,))])

train_dataset = datasets.MNIST(root='../data', train=True, transform=transform, download=True)
test_dataset = datasets.MNIST(root='../data', train=False, transform=transform, download=False)

# Data Loader (Input Pipeline)
train_loader = torch.utils.data.DataLoader(dataset=train_dataset, batch_size=bs, shuffle=True)
test_loader = torch.utils.data.DataLoader(dataset=test_dataset, batch_size=bs, shuffle=False)

In [4]:
labels = train_dataset.train_labels
indices0,indices1 = [], []
for i in range(0, 1):
    indices0 += (labels == i).nonzero().view(-1).tolist()
for i in range(1, 10):
    indices1 += (labels == i).nonzero().view(-1).tolist()
localset0, localset1 = Subset(train_dataset, indices0), Subset(train_dataset, indices1)
dataloader0, dataloader1 =DataLoader(localset0, batch_size=bs,shuffle=True), DataLoader(localset1, batch_size=bs,shuffle=True)

/home/xdy/anaconda3/lib/python3.7/site-packages/torchvision/datasets/mnist.py:52: UserWarning: train_labels has been renamed targets
  warnings.warn("train_labels has been renamed targets")


In [5]:
z_dim = 100
mnist_dim = train_dataset.train_data.size(1) * train_dataset.train_data.size(2)

G = Generator().to(gpu)
D = Discriminator().to(gpu)
criterion = nn.CrossEntropyLoss().to(gpu)
mse_criterion = nn.MSELoss().to(gpu)
mae_criterion = nn.L1Loss().to(gpu)
kl_criterion = nn.KLDivLoss(reduction='batchmean').to(gpu)
# optimizer
lr = 0.0002 
G_optimizer = optim.Adam(G.parameters(), lr = lr)
D_optimizer = optim.Adam(D.parameters(), lr = lr)

/home/xdy/anaconda3/lib/python3.7/site-packages/torchvision/datasets/mnist.py:62: UserWarning: train_data has been renamed data
  warnings.warn("train_data has been renamed data")


In [6]:
def zoo(D, x_fake, y_fake):
    grad_est = torch.zeros_like(x_fake).to(gpu)
    #reduction='none'
    criterion = nn.CrossEntropyLoss().cuda(gpu)
    m = 20
    epsilon = 0.1
    N = x_fake.size(0)
    C = x_fake.size(1)
    S = x_fake.size(2)
    d = S**2 * C
    
    lossG_target = criterion(D(torch.tanh(x_fake)),y_fake)
    
    for i in range(m):
        u = torch.randn(x_fake.size()).cuda(gpu)
        u_flat = u.view([N, -1])
        u_norm = u / torch.norm(u_flat, dim=1).view([-1, 1, 1, 1])
        x_mod_pre = x_fake + (epsilon * u_norm)
        Tout = D(torch.tanh(x_mod_pre))
        
        lossG_target_mod = criterion(Tout, y_fake)
        grad_est += (
                (d / m) * (lossG_target_mod - lossG_target) / epsilon
            ).view([-1, 1, 1, 1]) * u_norm
        
    grad_est /= N
    #return grad_est
    grad_est_flat = grad_est.view([N, -1])
    x_det_pre = x_fake.detach()
    x_det_pre.requires_grad = True
    x_det_pre.retain_grad()
    Tout = D(torch.tanh(x_det_pre))
    lossG_det = criterion(Tout, y_fake)
    lossG_det.backward()
    grad_true_flat = x_det_pre.grad.view([N, -1])

    cos = nn.CosineSimilarity(dim=1)
    cs = cos(grad_true_flat, grad_est_flat)
    mag_ratio = grad_est_flat.norm(2, dim=1) / grad_true_flat.norm(2, dim=1)
    lossG = lossG_det.detach()
    return lossG.mean(), cs.mean(), mag_ratio.mean(), grad_est


In [ ]:
epochs = 400
local_ep = 5
D.train()
G.train()
for epoch in range(epochs):
    for e in range(local_ep):
        for pri_x, pri_y in dataloader0:
            pri_x, pri_y = pri_x.to(gpu), pri_y.to(gpu)
            D.zero_grad()
            pri_logit = D(pri_x)
            loss = criterion(pri_logit, pri_y)
            loss.backward()
            D_optimizer.step()
    acc, _ = test_inference(D, test_loader)
    print(f"Epoch: {epoch} | Local Epoch: {e}: Loss: {loss.item()}, Acc: {acc}")
    
    #training public dataset for distillation including training discriminator of GAN training. 
    #Also, training shadow model
    for pub_x, pub_y in dataloader1:
        pub_x, pub_y = pub_x.to(gpu), pub_y.to(gpu)
        D.zero_grad()
        pub_logit = D(pub_x)
        D_real_loss = criterion(pub_logit, pub_y)
        
        # train discriminator on facke
        z = Variable(torch.randn(pub_x.size(0), z_dim).to(device))
        x_fake, y_fake = G(z), Variable(torch.zeros(pub_y.size()).fill_(10).long().to(gpu))
        D_fake_output = D(x_fake)
        D_fake_loss = criterion(D_fake_output, y_fake)
        
        # gradient backprop & optimize ONLY D's parameters
        D_loss = D_real_loss + D_fake_loss
        D_loss.backward()
        D_optimizer.step()
        

        G.zero_grad()

        z = Variable(torch.randn(pub_x.size(0), z_dim).to(gpu))
        y = Variable(torch.zeros(pub_y.size()).fill_(0).long().to(gpu))

        G_output = G(z)
        #estimate_grad, D_fake_loss = zeroth_order_optim(D, criterion, G_output, y)
        loss_g, cs, mag_ratio, estimate_grad = zoo(D, G_output, y)
        #print(f"estimate_grad: {estimate_grad.detach().clone()}")
        print(f"loss_g: {loss_g.item()} | cs: {cs.item()} | mag_ratio: {mag_ratio.item()}")
        #estimate_grad = zoo(D, G_output, y)
        G_output.backward(estimate_grad)
        G_optimizer.step()
#     if epoch % 10 == 0:
#         stat_num(D, S, test_loader)
#     print(f"Epoch: {epoch} | Model Extraction Acc: {test_error(D, S, test_loader)}")
    #print(f"Epoch: {epoch} | G_loss: {D_fake_loss.item()}, D_loss: {D_loss.item()}")
    with torch.no_grad():
        test_z = Variable(torch.randn(50, z_dim).to(device))
        generated = G(test_z)
        #out0grid = torchvision.utils.make_grid(generated.view(generated.size(0), 1, 28, 28), nrow=50)
        out0grid = torchvision.utils.make_grid(generated, nrow=50)
        writer.add_image('images', out0grid, epoch)
writer.close()

Epoch: 0 | Local Epoch: 4: Loss: 0.13018064200878143, Acc: 0.098
loss_g: 1.7683653831481934 | cs: 0.01686222478747368 | mag_ratio: 0.6972754597663879
loss_g: 3.390244960784912 | cs: 0.007931278087198734 | mag_ratio: 0.3561762869358063
loss_g: 6.539034843444824 | cs: 0.020194480195641518 | mag_ratio: 0.8781278729438782
loss_g: 10.22313404083252 | cs: 0.012362689711153507 | mag_ratio: 0.502827525138855
loss_g: 13.576739311218262 | cs: 0.011028106324374676 | mag_ratio: 0.7013588547706604
loss_g: 16.176918029785156 | cs: 0.014878739602863789 | mag_ratio: 0.7363856434822083
loss_g: 17.905458450317383 | cs: 0.01495968084782362 | mag_ratio: 0.7353651523590088
loss_g: 19.158462524414062 | cs: 0.009702266193926334 | mag_ratio: 0.5125657320022583
loss_g: 20.30034828186035 | cs: 0.013980465941131115 | mag_ratio: 0.6900361776351929
loss_g: 21.123994827270508 | cs: 0.016486449167132378 | mag_ratio: 0.721375584602356
loss_g: 22.086156845092773 | cs: 0.011509082280099392 | mag_ratio: 0.54504400491714

loss_g: 37.015769958496094 | cs: 0.01650926098227501 | mag_ratio: 0.7445604801177979
loss_g: 36.974674224853516 | cs: 0.014781464822590351 | mag_ratio: 0.670831561088562
loss_g: 37.025794982910156 | cs: 0.01644081063568592 | mag_ratio: 0.7316921949386597
loss_g: 37.34205627441406 | cs: 0.008609756827354431 | mag_ratio: 0.5733166933059692
loss_g: 37.63490676879883 | cs: 0.015720514580607414 | mag_ratio: 0.8204736113548279
loss_g: 37.6447868347168 | cs: 0.012794148176908493 | mag_ratio: 0.7249012589454651
loss_g: 37.667572021484375 | cs: 0.0169138852506876 | mag_ratio: 0.7538583278656006
loss_g: 37.630680084228516 | cs: 0.013070781715214252 | mag_ratio: 0.6959282755851746
loss_g: 37.70232391357422 | cs: 0.013684089295566082 | mag_ratio: 0.5952568054199219
loss_g: 37.89509201049805 | cs: 0.014447818510234356 | mag_ratio: 0.5667665600776672
loss_g: 38.066551208496094 | cs: 0.012295924127101898 | mag_ratio: 0.6527391672134399
loss_g: 38.125938415527344 | cs: 0.014661080203950405 | mag_ratio

loss_g: 45.869930267333984 | cs: 0.01049031037837267 | mag_ratio: 0.7953742742538452
loss_g: 45.81487274169922 | cs: 0.008145416155457497 | mag_ratio: 0.5352205038070679
loss_g: 45.55192947387695 | cs: 0.015189268626272678 | mag_ratio: 0.6883202791213989
loss_g: 45.50099182128906 | cs: 0.01435177307575941 | mag_ratio: 0.6487374901771545
loss_g: 45.66440963745117 | cs: 0.014325310476124287 | mag_ratio: 0.6935964822769165
loss_g: 45.99394607543945 | cs: 0.013249827548861504 | mag_ratio: 0.5320795774459839
loss_g: 46.04374694824219 | cs: 0.012477469630539417 | mag_ratio: 0.7626144886016846
loss_g: 46.033016204833984 | cs: 0.016337720677256584 | mag_ratio: 0.7588555812835693
loss_g: 45.833961486816406 | cs: 0.011811599135398865 | mag_ratio: 0.5832704305648804
loss_g: 45.73686218261719 | cs: 0.012369181029498577 | mag_ratio: 0.5725616812705994
loss_g: 45.73670959472656 | cs: 0.013068214058876038 | mag_ratio: 0.5703110098838806
loss_g: 45.829010009765625 | cs: 0.009931972250342369 | mag_rati

loss_g: 47.74005889892578 | cs: 0.01148235984146595 | mag_ratio: 0.6702183485031128
loss_g: 47.93406677246094 | cs: 0.010745751671493053 | mag_ratio: 0.8175654411315918
loss_g: 48.040035247802734 | cs: 0.013370382599532604 | mag_ratio: 0.6783810257911682
loss_g: 48.094505310058594 | cs: 0.015747658908367157 | mag_ratio: 0.7059516906738281
loss_g: 48.09865188598633 | cs: 0.019078804180026054 | mag_ratio: 0.7776115536689758
loss_g: 47.676448822021484 | cs: 0.015339606441557407 | mag_ratio: 0.9744175672531128
loss_g: 47.294189453125 | cs: 0.009560254402458668 | mag_ratio: 0.7874541878700256
loss_g: 47.0814094543457 | cs: 0.014713236130774021 | mag_ratio: 0.7902525067329407
loss_g: 46.98777770996094 | cs: 0.013127579353749752 | mag_ratio: 0.800585925579071
loss_g: 46.650325775146484 | cs: 0.014494952745735645 | mag_ratio: 0.6154064536094666
loss_g: 44.712581634521484 | cs: 0.012454036623239517 | mag_ratio: 0.8478543162345886
loss_g: 44.77846145629883 | cs: 0.013624711893498898 | mag_ratio:

loss_g: 42.18601989746094 | cs: 0.014846675097942352 | mag_ratio: 0.7088580131530762
loss_g: 42.34085464477539 | cs: 0.009692166931927204 | mag_ratio: 0.852809727191925
loss_g: 42.658199310302734 | cs: 0.018825214356184006 | mag_ratio: 0.7896377444267273
loss_g: 43.35482406616211 | cs: 0.01772960275411606 | mag_ratio: 0.7574507594108582
loss_g: 44.01047897338867 | cs: 0.00712527334690094 | mag_ratio: 1.417104721069336
loss_g: 44.459083557128906 | cs: 0.017023231834173203 | mag_ratio: 0.7650184631347656
loss_g: 44.65056228637695 | cs: 0.007030352018773556 | mag_ratio: 0.9986863732337952
loss_g: 44.39018249511719 | cs: 0.012168621644377708 | mag_ratio: 0.522226870059967
loss_g: 43.96604919433594 | cs: 0.006310675758868456 | mag_ratio: 1.0459736585617065
loss_g: 43.41259765625 | cs: 0.010250067338347435 | mag_ratio: 1.484007477760315
loss_g: 43.01646041870117 | cs: 0.008395664393901825 | mag_ratio: 1.1623241901397705
loss_g: 42.7182731628418 | cs: 0.014866323210299015 | mag_ratio: 0.96285

...

loss_g: 1.7447195053100586 | cs: 0.012701652012765408 | mag_ratio: 0.9475675821304321
loss_g: 1.8412251472473145 | cs: 0.01334357913583517 | mag_ratio: 1.0139073133468628
loss_g: 1.8133764266967773 | cs: 0.016677631065249443 | mag_ratio: 1.038899302482605
loss_g: 1.8209998607635498 | cs: 0.018958669155836105 | mag_ratio: 0.9597021341323853
loss_g: 1.824248194694519 | cs: 0.015200807712972164 | mag_ratio: 0.9119040369987488
loss_g: 1.7275702953338623 | cs: 0.01263442263007164 | mag_ratio: 0.7438924908638
loss_g: 1.7277809381484985 | cs: 0.019248660653829575 | mag_ratio: 1.1116706132888794
loss_g: 1.6994848251342773 | cs: 0.017981979995965958 | mag_ratio: 0.9060853123664856
loss_g: 1.7838481664657593 | cs: 0.019545001909136772 | mag_ratio: 0.8664069771766663
loss_g: 1.7673027515411377 | cs: 0.0148688443005085 | mag_ratio: 0.7146294713020325
loss_g: 1.699867606163025 | cs: 0.01761133223772049 | mag_ratio: 0.9390463829040527
loss_g: 1.725149393081665 | cs: 0.014224991202354431 | mag_ratio:

loss_g: 0.6648772954940796 | cs: 0.010351032949984074 | mag_ratio: 1.6376436948776245
loss_g: 0.6217271089553833 | cs: 0.010937632992863655 | mag_ratio: 1.2676647901535034
loss_g: 0.6575756072998047 | cs: 0.009028484113514423 | mag_ratio: 1.5483229160308838
loss_g: 0.5691654086112976 | cs: 0.006592412479221821 | mag_ratio: 1.3927347660064697
loss_g: 0.5716296434402466 | cs: 0.016599072143435478 | mag_ratio: 1.9725990295410156
loss_g: 0.5565225481987 | cs: 0.006127070169895887 | mag_ratio: 1.408497929573059
loss_g: 0.4824511408805847 | cs: 0.014203599654138088 | mag_ratio: 1.7903084754943848
loss_g: 0.547200620174408 | cs: 0.006886343937367201 | mag_ratio: 1.3265020847320557
loss_g: 0.45016878843307495 | cs: 0.008542533032596111 | mag_ratio: 1.544148564338684
loss_g: 0.4056875705718994 | cs: 0.009692545048892498 | mag_ratio: 2.281219244003296
loss_g: 0.48342037200927734 | cs: 0.011266667395830154 | mag_ratio: 2.6713366508483887
loss_g: 0.4403824508190155 | cs: 0.007177973631769419 | mag

loss_g: 0.14952895045280457 | cs: 0.005216511432081461 | mag_ratio: 5.302814960479736
loss_g: 0.23064039647579193 | cs: 0.005656378343701363 | mag_ratio: 6.379045486450195
loss_g: 0.26584118604660034 | cs: 0.009626797400414944 | mag_ratio: 4.597968101501465
loss_g: 0.3025422692298889 | cs: 0.013409548439085484 | mag_ratio: 4.881518363952637
loss_g: 0.4835107922554016 | cs: 0.012505553662776947 | mag_ratio: 11.0555419921875
loss_g: 0.55484938621521 | cs: 0.015018908306956291 | mag_ratio: 4.891364097595215
loss_g: 0.5715324878692627 | cs: 0.008850089274346828 | mag_ratio: 3.5064055919647217
loss_g: 0.6323826313018799 | cs: 0.009493477642536163 | mag_ratio: 3.7848641872406006
loss_g: 0.7556094527244568 | cs: 0.011618507094681263 | mag_ratio: 4.03397798538208
loss_g: 0.5998525023460388 | cs: 0.006491225678473711 | mag_ratio: 4.6748175621032715
loss_g: 0.5752424001693726 | cs: 0.006283551454544067 | mag_ratio: 3.5773003101348877
loss_g: 0.6558576822280884 | cs: 0.01294270996004343 | mag_rat

loss_g: 0.23833288252353668 | cs: 0.011341452598571777 | mag_ratio: 2.9171316623687744
loss_g: 0.2007817029953003 | cs: 0.01249110046774149 | mag_ratio: 2.167372703552246
loss_g: 0.1973058134317398 | cs: 0.010998019948601723 | mag_ratio: 2.7838878631591797
loss_g: 0.29411810636520386 | cs: 0.00625644950196147 | mag_ratio: 3.804302215576172
loss_g: 0.18956060707569122 | cs: 0.008415975607931614 | mag_ratio: 3.082266092300415
loss_g: 0.23490236699581146 | cs: 0.007246206980198622 | mag_ratio: 3.0612902641296387
loss_g: 0.26395779848098755 | cs: 0.005784328561276197 | mag_ratio: 3.4140453338623047
loss_g: 0.2354874461889267 | cs: 0.009985801763832569 | mag_ratio: 2.359919548034668
loss_g: 0.21502685546875 | cs: 0.01289413869380951 | mag_ratio: 2.989807605743408
loss_g: 0.3143918216228485 | cs: 0.010770742781460285 | mag_ratio: 3.507922649383545
loss_g: 0.18406669795513153 | cs: 0.011440938338637352 | mag_ratio: 2.446521043777466
loss_g: 0.17907100915908813 | cs: 0.0071911984123289585 | ma

loss_g: 0.08679720759391785 | cs: 0.01705170050263405 | mag_ratio: 2.8999431133270264
loss_g: 0.08535179495811462 | cs: 0.009663617238402367 | mag_ratio: 2.1704001426696777
loss_g: 0.11219990998506546 | cs: 0.012050453573465347 | mag_ratio: 3.252070426940918
loss_g: 0.14249970018863678 | cs: 0.008082956075668335 | mag_ratio: 5.705899715423584
loss_g: 0.08534485101699829 | cs: 0.01288336981087923 | mag_ratio: 2.4398059844970703
loss_g: 0.11443675309419632 | cs: 0.004755426663905382 | mag_ratio: 2.7844176292419434
loss_g: 0.13529877364635468 | cs: 0.009154129773378372 | mag_ratio: 3.813840866088867
loss_g: 0.14158685505390167 | cs: 0.006987116299569607 | mag_ratio: 4.373478412628174
loss_g: 0.07846936583518982 | cs: 0.011083262041211128 | mag_ratio: 2.1401169300079346
loss_g: 0.15416789054870605 | cs: 0.0062947701662778854 | mag_ratio: 4.6259613037109375
loss_g: 0.11511165648698807 | cs: 0.009436395019292831 | mag_ratio: 3.6373841762542725
loss_g: 0.15929864346981049 | cs: 0.013431138359

In [8]:
with torch.no_grad():
    test_z = Variable(torch.randn(300, z_dim).to(device))
    generated = G(test_z)
    #out0grid = torchvision.utils.make_grid(generated.view(generated.size(0), 1, 28, 28), nrow=20)
    out0grid = torchvision.utils.make_grid(generated, nrow=20)
    fig, ax = subplots(figsize=(32, 32))
    ax.imshow(out0grid.detach().permute(1, 2, 0).cpu())

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


In [ ]:
def zeroth_order_optim(D, criterion, x_fake, y_fake):
    criterion = nn.CrossEntropyLoss(reduction='none')
    #m = 5
    m = 19
    pre_x = True
    epsilon = 1e-7
    #criterion = nn.NLLLoss().to(gpu)
    with torch.no_grad():
        # Sample unit noise vector
        N = x_fake.size(0)
        C = x_fake.size(1)
        S = x_fake.size(2)
        dim = S**2 * C

        u = np.random.randn(N * m * dim).reshape(-1, m, dim) # generate random points from normal distribution

        d = np.sqrt(np.sum(u ** 2, axis = 2)).reshape(-1, m, 1)  # map to a uniform distribution on a unit sphere
        u = torch.Tensor(u / d).view(-1, m, C, S, S)
        u = torch.cat((u, torch.zeros(N, 1, C, S, S)), dim = 1) # Shape N, m + 1, S^2

            

        u = u.view(-1, m + 1, C, S, S)

        evaluation_points = (x_fake.view(-1, 1, C, S, S).cpu() + epsilon * u).view(-1, C, S, S)
        if pre_x: 
            evaluation_points = torch.tanh(evaluation_points) # Apply args.G_activation function
        # Compute the approximation sequentially to allow large values of m
        #print(f"{evaluation_points.size()}")
        
        x_b = evaluation_points.size(0)
        y_b = y_fake.size(0)
        y_fake = y_fake.repeat(x_b//y_b)
        pred_victim = []
        max_number_points = 32*156  # Hardcoded value to split the large evaluation_points tensor to fit in GPU
        
        for i in (range(N * m // max_number_points + 1)): 
            pts = evaluation_points[i * max_number_points: (i+1) * max_number_points]
            #print(f"{pts.size()}")
            pts = pts.to(gpu)
            #print(f"pts: {pts.size()}")
            pred_victim_pts = D(pts).detach()
            pred_victim.append(pred_victim_pts)
            
        pred_victim = torch.cat(pred_victim, dim=0).to(gpu)
        u = u.to(gpu)
        #print(f"{pred_victim.size()}, {y_fake.size()}")
        #pred_victim -= pred_victim.mean(dim=1).view(-1, 1).detach()
        #print(f"{pred_victim.size()}")
        #pred_victim = F.log_softmax(pred_victim, dim=1)
        #print(pred_victim.size())
        
        #pred_victim = pred_victim.view(-1, 1).detach()
        #print(f"{pred_victim.size()}, {y_fake.size()}")
        D_fake_loss = criterion(pred_victim, y_fake)
        #print(D_fake_loss.size())
        #print(f"d_fake_loss: {D_fake_loss.size()}")
        D_fake_loss = D_fake_loss.view(-1, m + 1)
        #print(f"reshape: {D_fake_loss.size()}")
        # Compute difference following each direction
        differences = D_fake_loss[:, :-1] - D_fake_loss[:, -1].view(-1, 1)
        differences = differences.view(-1, m, 1, 1, 1)

        # Formula for Forward Finite Differences
        gradient_estimates = 1 / epsilon * differences * u[:, :-1]
        gradient_estimates *= dim   
        gradient_estimates = gradient_estimates.mean(dim = 1).view(-1, C, S, S)
        loss_G = D_fake_loss[:, -1].mean()
        return gradient_estimates.detach(), loss_G
